<a href="https://colab.research.google.com/github/rayeeed/UFP_Project/blob/main/UFP_svr_lr_xgb_ada_eval.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
import pandas as pd
import numpy as np
from sklearn.model_selection import train_test_split
from sklearn.tree import DecisionTreeRegressor
from sklearn.ensemble import IsolationForest
from sklearn.ensemble import RandomForestRegressor
from sklearn.linear_model import LogisticRegression
from sklearn.linear_model import LinearRegression
from xgboost import XGBRegressor
#from sklearn.model_selection import LeaveOneOut
from sklearn.model_selection import cross_val_score,cross_val_predict
import matplotlib.pyplot as plt
from sklearn.metrics import accuracy_score
from sklearn.metrics import r2_score
from sklearn.metrics import mean_absolute_error
from sklearn.pipeline import Pipeline
from sklearn.feature_selection import SequentialFeatureSelector
from sklearn.neighbors import KNeighborsClassifier
from sklearn.linear_model import RidgeCV
from sklearn.feature_selection import mutual_info_regression
from sklearn.feature_selection import SelectFromModel
from time import time
from sklearn.linear_model import RidgeCV
from sklearn.model_selection import RepeatedKFold
from xgboost import XGBRegressor
from sklearn.metrics import mean_squared_error
import seaborn as sns
from sklearn.preprocessing import Normalizer,MinMaxScaler,StandardScaler,RobustScaler
from sklearn.model_selection import GridSearchCV
from sklearn.svm import SVR
from sklearn.ensemble import RandomForestRegressor
from sklearn.linear_model import Ridge, Lasso, BayesianRidge
from sklearn.ensemble import GradientBoostingRegressor
from sklearn.feature_selection import RFE,RFECV
from sklearn.linear_model import (HuberRegressor,
                              	RANSACRegressor, TheilSenRegressor)

In [ ]:
!pip install optuna
import optuna

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 362.8/362.8 kB 7.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 233.0/233.0 kB 14.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 78.6/78.6 kB 5.6 MB/s eta 0:00:00


In [ ]:
from sklearn.model_selection import StratifiedShuffleSplit
from sklearn.preprocessing import KBinsDiscretizer

# Load the dataset
df = pd.read_excel('/content/drive/MyDrive/datasets_Rayeed_GSV_POI_LU/model_35.xlsx', index_col='site_name')

# Drop unnecessary columns
df.drop(['Site_type', 'OID'], inplace=True, axis=1)

# Separate the target variable and features
y = df['Mean PNC (# / cm3)']
X = df.drop(['Mean PNC (# / cm3)', 'Mean PM2.5 (µg/m3)'], axis=1)

In [ ]:
# Discretize the target variable into bins using 'quantile' strategy
binner = KBinsDiscretizer(n_bins=5, encode='ordinal', strategy='quantile')
y_binned = binner.fit_transform(y.values.reshape(-1, 1)).flatten()

# Perform stratified train-test split
split = StratifiedShuffleSplit(n_splits=1, test_size=.2, random_state=42)
for train_index, test_index in split.split(X, y_binned):
    X_train, X_test = X.iloc[train_index], X.iloc[test_index]
    y_train, y_test = y.iloc[train_index], y.iloc[test_index]

# Check the distribution of bins in the train and test sets
print("Train bin distribution:\n", pd.value_counts(y_binned[train_index], sort=False))
print("Test bin distribution:\n", pd.value_counts(y_binned[test_index], sort=False))

# Output the resulting dataframes
print("X_train:\n", X_train.head())
print("y_train:\n", y_train.head())
print("X_test:\n", X_test.head())
print("y_test:\n", y_test.head())

Train bin distribution:
 0.0    5
1.0    6
3.0    5
4.0    6
2.0    6
Name: count, dtype: int64
Test bin distribution:
 0.0    2
1.0    1
3.0    2
2.0    1
4.0    1
Name: count, dtype: int64
X_train:
                  gsv_wall_p100  gsv_building_p100  gsv_house_p100  \
site_name                                                           
Uttara_Sector1        6.797307          32.993471        0.232041   
Azimpur               0.000000           0.000000        0.000000   
US_Embassy            3.237500           2.430000        0.000000   
Elephant_road         0.070000          42.007500        0.000000   
Square_hospital      59.247500           0.000000        0.000000   

                 gsv_awning_p100  gsv_sky_p100  gsv_earth_p100  gsv_tree_p100  \
site_name                                                                       
Uttara_Sector1           0.09694     19.991354         3.48166      15.913745   
Azimpur                  0.00000      0.000000         0.00000       0.0

<ipython-input-3-a1486702b7a8>:12: FutureWarning: pandas.value_counts is deprecated and will be removed in a future version. Use pd.Series(obj).value_counts() instead.
  print("Train bin distribution:\n", pd.value_counts(y_binned[train_index], sort=False))
<ipython-input-3-a1486702b7a8>:13: FutureWarning: pandas.value_counts is deprecated and will be removed in a future version. Use pd.Series(obj).value_counts() instead.
  print("Test bin distribution:\n", pd.value_counts(y_binned[test_index], sort=False))


In [ ]:
from scipy.stats import ks_2samp
ks_statistic, p_value = ks_2samp(y_train, y_test)

print(f"K-S statistic: {ks_statistic}")
print(f"P-value: {p_value}")

# Interpretation
alpha = 0.05
if p_value < alpha:
    print("The null hypothesis is rejected. The distributions of the train and test sets are different.")
else:
    print("The null hypothesis cannot be rejected. The distributions of the train and test sets are the same.")

K-S statistic: 0.25
P-value: 0.842454033893869
The null hypothesis cannot be rejected. The distributions of the train and test sets are the same.


In [ ]:
# Apply Kolmogorov-Smirnov test for each feature
ks_results = {}
failed_features = []
alpha = 0.05
for feature in X.columns:
    ks_statistic, p_value = ks_2samp(X_train[feature], X_test[feature])
    ks_results[feature] = {'ks_statistic': ks_statistic, 'p_value': p_value}
    if p_value < alpha:
        failed_features.append(feature)

# Print K-S test results for each feature
for feature, result in ks_results.items():
    print(f"Feature: {feature}")
    print(f"K-S statistic: {result['ks_statistic']}")
    print(f"P-value: {result['p_value']}")
    if result['p_value'] < alpha:
        print("The null hypothesis is rejected. The distributions of the train and test sets are different for this feature.\n")
    else:
        print("The null hypothesis cannot be rejected. The distributions of the train and test sets are the same for this feature.\n")

# Print features that failed the K-S test
if failed_features:
    print("Features that failed the K-S test (null hypothesis rejected):")
    for feature in failed_features:
        print(f"- {feature}")
else:
    print("All features passed the K-S test (null hypothesis not rejected).")

Feature: gsv_wall_p100
K-S statistic: 0.32142857142857145
P-value: 0.5556032252116138
The null hypothesis cannot be rejected. The distributions of the train and test sets are the same for this feature.

Feature: gsv_building_p100
K-S statistic: 0.17857142857142858
P-value: 0.9883820703931286
The null hypothesis cannot be rejected. The distributions of the train and test sets are the same for this feature.

Feature: gsv_house_p100
K-S statistic: 0.10714285714285714
P-value: 0.9999998512905011
The null hypothesis cannot be rejected. The distributions of the train and test sets are the same for this feature.

Feature: gsv_awning_p100
K-S statistic: 0.21428571428571427
P-value: 0.9411846496106786
The null hypothesis cannot be rejected. The distributions of the train and test sets are the same for this feature.

Feature: gsv_sky_p100
K-S statistic: 0.2857142857142857
P-value: 0.7050303962215889
The null hypothesis cannot be rejected. The distributions of the train and test sets are the same

In [ ]:
X_train_dropped = X_train.drop(columns=failed_features)
X_test_dropped = X_test.drop(columns=failed_features)

In [ ]:
trans = StandardScaler()
X_st = trans.fit_transform(X_train_dropped)
X_st = pd.DataFrame(X_st, columns=X_train_dropped.columns, index=X_train_dropped.index)

In [ ]:
X_test_st = trans.transform(X_test_dropped)
X_test_st = pd.DataFrame(X_test_st, columns=X_test_dropped.columns, index=X_test_dropped.index)

In [ ]:
X_Pred = pd.read_excel('/content/drive/MyDrive/datasets_Rayeed_GSV_POI_LU/combined_total_v4.0.xlsx', index_col='OID_')

In [ ]:
col=X_st.columns
X_Pred_f1 = X_Pred[col]
X_Pred_f2= X_Pred_f1

In [ ]:
x_pred_st= trans.transform(X_Pred_f2)
x_pred_st = pd.DataFrame(x_pred_st, columns = X_Pred_f2.columns,index=X_Pred_f2.index)

In [ ]:
Feature_list = [['RdAll_150', 'gsv_house_p750', 'gsv_signboard_p250', 'RdclP_150', 'gsv_plant_p250'],['RdAll_150', 'gsv_house_p750', 'RdclP_150', 'gsv_plant_p250'],['RdAll_150', 'gsv_house_p750', 'gsv_bus_p1000', 'RdclP_150', 'gsv_plant_p250'],['RdAll_150', 'gsv_house_p750', 'gsv_signboard_p250', 'RdL3_1000', 'RdclP_150']]

In [ ]:
import itertools
import optuna
import pandas as pd
from sklearn.metrics import mean_squared_error, r2_score
from sklearn.model_selection import cross_val_predict
from xgboost import XGBRegressor
from sklearn.tree import DecisionTreeRegressor
from sklearn.ensemble import AdaBoostRegressor, RandomForestRegressor

# Mandatory features
mandatory_features = ['RdAll_150', 'gsv_house_p750']

# Feature list to evaluate
Feature_list = [
    ['RdAll_150', 'gsv_house_p750', 'gsv_signboard_p250', 'RdclP_150', 'gsv_plant_p250'],
    ['RdAll_150', 'gsv_house_p750', 'RdclP_150', 'gsv_plant_p250'],
    ['RdAll_150', 'gsv_house_p750', 'gsv_bus_p1000', 'RdclP_150', 'gsv_plant_p250'],
    ['RdAll_150', 'gsv_house_p750', 'gsv_signboard_p250', 'RdL3_1000', 'RdclP_150']
]

# Function to run the optimization and evaluate the model
def evaluate_model(features, model_type):
    X_Train = X_st[features]
    X_test = X_test_st[features]

    def objective(trial):
        if model_type == 'XGBRegressor':
            learning_rate = trial.suggest_float('learning_rate', 0.001, 1.5)
            n_estimators = trial.suggest_int('n_estimators', 50, 2000)
            reg_alpha = trial.suggest_float('reg_alpha', 0.01, 100)
            reg_lambda = trial.suggest_float('reg_lambda', 0.01, 10)
            model = XGBRegressor(booster='gblinear',
                                 n_estimators=n_estimators,
                                 learning_rate=learning_rate,
                                 reg_alpha=reg_alpha,
                                 reg_lambda=reg_lambda,
                                 objective="reg:squarederror",
                                 seed=42)
        elif model_type == 'AdaBoostRegressor':
            n_estimators = trial.suggest_int("n_estimators", 50, 1000)
            learning_rate = trial.suggest_float("learning_rate", 0.001, 2.0)
            max_depth = trial.suggest_int("max_depth", 1, 50)
            base_estimator = DecisionTreeRegressor(max_depth=max_depth)
            model = AdaBoostRegressor(base_estimator=base_estimator,
                                      n_estimators=n_estimators,
                                      learning_rate=learning_rate,
                                      random_state=42)
        elif model_type == 'RandomForestRegressor':
            n_estimators = trial.suggest_int("n_estimators", 50, 2000)
            max_depth = trial.suggest_int("max_depth", 3, 50)
            min_samples_split = trial.suggest_int("min_samples_split", 2, 40)
            min_samples_leaf = trial.suggest_int("min_samples_leaf", 1, 40)
            model = RandomForestRegressor(n_estimators=n_estimators,
                                          max_depth=max_depth,
                                          min_samples_split=min_samples_split,
                                          min_samples_leaf=min_samples_leaf,
                                          random_state=42)

        predicted = cross_val_predict(model, X_Train, y_train, cv=10)
        return mean_squared_error(y_train, predicted, squared=False)

    study = optuna.create_study(direction='minimize', study_name=f"{model_type}_RMSE")
    study.optimize(objective, n_trials=100)  # Adjust n_trials as necessary

    best_params = study.best_params
    if model_type == 'XGBRegressor':
        model = XGBRegressor(booster='gblinear',
                             learning_rate=best_params['learning_rate'],
                             n_estimators=best_params['n_estimators'],
                             reg_alpha=best_params['reg_alpha'],
                             reg_lambda=best_params['reg_lambda'],
                             objective="reg:squarederror",
                             seed=42)
    elif model_type == 'AdaBoostRegressor':
        base_estimator = DecisionTreeRegressor(max_depth=best_params['max_depth'])
        model = AdaBoostRegressor(base_estimator=base_estimator,
                                  n_estimators=best_params['n_estimators'],
                                  learning_rate=best_params['learning_rate'],
                                  random_state=42)
    elif model_type == 'RandomForestRegressor':
        model = RandomForestRegressor(n_estimators=best_params['n_estimators'],
                                      max_depth=best_params['max_depth'],
                                      min_samples_split=best_params['min_samples_split'],
                                      min_samples_leaf=best_params['min_samples_leaf'],
                                      random_state=42)

    model.fit(X_Train, y_train)

    pred_train = model.predict(X_Train)
    rmse_train = mean_squared_error(y_train, pred_train, squared=False)
    r2_train = r2_score(y_train, pred_train)

    predicted = cross_val_predict(model, X_Train, y_train, cv=10)
    rmse_cv = mean_squared_error(y_train, predicted, squared=False)
    r2_cv = r2_score(y_train, predicted)

    predicted_test = model.predict(X_test)
    rmse_test = mean_squared_error(y_test, predicted_test, squared=False)
    r2_test = r2_score(y_test, predicted_test)

    return {
        "features": features,
        "model": model_type,
        "rmse_train": rmse_train,
        "r2_train": r2_train,
        "rmse_cv": rmse_cv,
        "r2_cv": r2_cv,
        "rmse_test": rmse_test,
        "r2_test": r2_test
    }

# Evaluate the models using each set of features in the feature list and different model types
results = []
model_types = ['XGBRegressor', 'AdaBoostRegressor', 'RandomForestRegressor']

for feature_set in Feature_list:
    for model_type in model_types:
        print(f"Evaluating combination: {feature_set} with model: {model_type}")
        try:
            result = evaluate_model(feature_set, model_type)
            results.append(result)
        except ValueError as e:
            if "Input contains NaN" in str(e):
                print(f"Skipping combination due to NaN values: {feature_set}")
            else:
                raise e  # Raise the error if it's not due to NaN values

# Create a DataFrame to store the results
results_df = pd.DataFrame(results)

# Display the results
print(results_df.head())

# Save the results to a CSV file
results_df.to_csv("/content/drive/MyDrive/datasets_Rayeed_GSV_POI_LU/feature_selection_results_UFP_all.csv", index=False)


[I 2024-08-12 05:51:05,187] A new study created in memory with name: XGBRegressor_RMSE


Evaluating combination: ['RdAll_150', 'gsv_house_p750', 'gsv_signboard_p250', 'RdclP_150', 'gsv_plant_p250'] with model: XGBRegressor


[I 2024-08-12 05:51:14,393] Trial 0 finished with value: 16799.159047152254 and parameters: {'learning_rate': 0.5749983579089868, 'n_estimators': 336, 'reg_alpha': 58.24710593376794, 'reg_lambda': 7.625211486034213}. Best is trial 0 with value: 16799.159047152254.
[I 2024-08-12 05:51:19,950] Trial 1 finished with value: 14681.8359982664 and parameters: {'learning_rate': 0.8037185640942386, 'n_estimators': 1480, 'reg_alpha': 58.951458794796004, 'reg_lambda': 2.581571198385094}. Best is trial 1 with value: 14681.8359982664.
[I 2024-08-12 05:51:20,881] Trial 2 finished with value: 15472.278614383426 and parameters: {'learning_rate': 0.5205200190500067, 'n_estimators': 1249, 'reg_alpha': 31.685119989877524, 'reg_lambda': 3.7640952302095396}. Best is trial 1 with value: 14681.8359982664.
[I 2024-08-12 05:51:21,999] Trial 3 finished with value: 16903.73069923598 and parameters: {'learning_rate': 1.2149042435797381, 'n_estimators': 1541, 'reg_alpha': 67.68211945616352, 'reg_lambda': 8.1350889

Evaluating combination: ['RdAll_150', 'gsv_house_p750', 'gsv_signboard_p250', 'RdclP_150', 'gsv_plant_p250'] with model: AdaBoostRegressor


/usr/local/lib/python3.10/dist-packages/sklearn/ensemble/_base.py:156: FutureWarning: `base_estimator` was renamed to `estimator` in version 1.2 and will be removed in 1.4.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/sklearn/ensemble/_base.py:156: FutureWarning: `base_estimator` was renamed to `estimator` in version 1.2 and will be removed in 1.4.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/sklearn/ensemble/_base.py:156: FutureWarning: `base_estimator` was renamed to `estimator` in version 1.2 and will be removed in 1.4.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/sklearn/ensemble/_base.py:156: FutureWarning: `base_estimator` was renamed to `estimator` in version 1.2 and will be removed in 1.4.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/sklearn/ensemble/_base.py:156: FutureWarning: `base_estimator` was renamed to `estimator` in version 1.2 and will be removed in 1.4.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/sklearn/en

...

Evaluating combination: ['RdAll_150', 'gsv_house_p750', 'gsv_signboard_p250', 'RdL3_1000', 'RdclP_150'] with model: AdaBoostRegressor


/usr/local/lib/python3.10/dist-packages/sklearn/ensemble/_base.py:156: FutureWarning: `base_estimator` was renamed to `estimator` in version 1.2 and will be removed in 1.4.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/sklearn/ensemble/_base.py:156: FutureWarning: `base_estimator` was renamed to `estimator` in version 1.2 and will be removed in 1.4.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/sklearn/ensemble/_base.py:156: FutureWarning: `base_estimator` was renamed to `estimator` in version 1.2 and will be removed in 1.4.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/sklearn/ensemble/_base.py:156: FutureWarning: `base_estimator` was renamed to `estimator` in version 1.2 and will be removed in 1.4.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/sklearn/ensemble/_base.py:156: FutureWarning: `base_estimator` was renamed to `estimator` in version 1.2 and will be removed in 1.4.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/sklearn/en

Evaluating combination: ['RdAll_150', 'gsv_house_p750', 'gsv_signboard_p250', 'RdL3_1000', 'RdclP_150'] with model: RandomForestRegressor


[I 2024-08-12 07:52:00,505] Trial 0 finished with value: 18904.212275087746 and parameters: {'n_estimators': 1168, 'max_depth': 46, 'min_samples_split': 28, 'min_samples_leaf': 14}. Best is trial 0 with value: 18904.212275087746.
[I 2024-08-12 07:52:21,978] Trial 1 finished with value: 18909.449005153587 and parameters: {'n_estimators': 1559, 'max_depth': 37, 'min_samples_split': 15, 'min_samples_leaf': 14}. Best is trial 0 with value: 18904.212275087746.
[I 2024-08-12 07:52:36,916] Trial 2 finished with value: 18904.23431073515 and parameters: {'n_estimators': 1135, 'max_depth': 20, 'min_samples_split': 12, 'min_samples_leaf': 21}. Best is trial 0 with value: 18904.212275087746.
[I 2024-08-12 07:52:57,134] Trial 3 finished with value: 18908.41570775376 and parameters: {'n_estimators': 1573, 'max_depth': 16, 'min_samples_split': 33, 'min_samples_leaf': 20}. Best is trial 0 with value: 18904.212275087746.
[I 2024-08-12 07:53:18,576] Trial 4 finished with value: 18909.449005153587 and pa

                                            features                  model  \
0  [RdAll_150, gsv_house_p750, gsv_signboard_p250...           XGBRegressor   
1  [RdAll_150, gsv_house_p750, gsv_signboard_p250...      AdaBoostRegressor   
2  [RdAll_150, gsv_house_p750, gsv_signboard_p250...  RandomForestRegressor   
3  [RdAll_150, gsv_house_p750, RdclP_150, gsv_pla...           XGBRegressor   
4  [RdAll_150, gsv_house_p750, RdclP_150, gsv_pla...      AdaBoostRegressor   

    rmse_train  r2_train       rmse_cv     r2_cv     rmse_test   r2_test  
0  9127.859046  0.740744  10986.505967  0.624413  20109.777244  0.327166  
1  1276.994239  0.994926  10927.602665  0.628430  24274.442762  0.019625  
2  4599.270002  0.934178  11751.278579  0.570304  23071.339481  0.114397  
3  9966.093056  0.690941  11513.026272  0.587551  21059.542768  0.262110  
4  2200.000000  0.984940  11776.262444  0.568475  25103.613855 -0.048495  


# ***SVR Final Pred***

In [ ]:
from fastai.tabular.all import *
import optuna
import pandas as pd
from sklearn.metrics import mean_squared_error, r2_score

# Feature list to evaluate
Feature_list = [
    ['RdAll_150', 'gsv_house_p750', 'gsv_signboard_p250', 'RdclP_150', 'gsv_plant_p250'],
    ['RdAll_150', 'gsv_house_p750', 'RdclP_150', 'gsv_plant_p250'],
    ['RdAll_150', 'gsv_house_p750', 'gsv_bus_p1000', 'RdclP_150', 'gsv_plant_p250'],
    ['RdAll_150', 'gsv_house_p750', 'gsv_signboard_p250', 'RdL3_1000', 'RdclP_150']
]

# Function to run the optimization and evaluate the Fastai model
def evaluate_fastai_model(features):
    # Prepare data for Fastai
    df_train = X_st[features].copy()
    df_train['target'] = y_train.values
    df_test = X_test_st[features].copy()
    df_test['target'] = y_test.values

    def objective(trial):
        # Hyperparameters for the neural network
        n_layers = trial.suggest_int('n_layers', 1, 3)
        layer_sizes = [trial.suggest_int(f'n_units_l{i}', 10, 500) for i in range(n_layers)]
        learning_rate = trial.suggest_loguniform('learning_rate', 1e-5, 1e-1)

        # Create DataLoaders
        dls = TabularDataLoaders.from_df(
            df_train, path='.', y_names='target',
            cont_names=features, procs=[Normalize]
        )

        # Define and train the model
        learn = tabular_learner(dls, layers=layer_sizes, metrics=rmse, lr=learning_rate)
        learn.fit_one_cycle(10, lr_max=learning_rate)

        # Get RMSE on training set
        train_preds, train_targets = learn.get_preds(dl=dls.train)
        rmse_train = mean_squared_error(train_targets, train_preds, squared=False)

        return rmse_train

    study = optuna.create_study(direction='minimize', study_name="Fastai_NN_RMSE")
    study.optimize(objective, n_trials=100)  # Adjust n_trials as necessary

    best_params = study.best_params
    n_layers = best_params['n_layers']
    layer_sizes = [best_params[f'n_units_l{i}'] for i in range(n_layers)]
    learning_rate = best_params['learning_rate']

    # Create final model with best hyperparameters
    dls = TabularDataLoaders.from_df(
        df_train, path='.', y_names='target',
        cont_names=features, procs=[Normalize]
    )
    learn = tabular_learner(dls, layers=layer_sizes, metrics=rmse, lr=learning_rate)
    learn.fit_one_cycle(10, lr_max=learning_rate)

    # Evaluate model on train set
    train_preds, train_targets = learn.get_preds(dl=dls.train)
    rmse_train = mean_squared_error(train_targets, train_preds, squared=False)
    r2_train = r2_score(train_targets, train_preds)

    # Evaluate model on test set
    test_dl = learn.dls.test_dl(df_test)
    test_preds, test_targets = learn.get_preds(dl=test_dl)
    rmse_test = mean_squared_error(test_targets, test_preds, squared=False)
    r2_test = r2_score(test_targets, test_preds)

    return {
        "features": features,
        "model": "Fastai_NeuralNet",
        "rmse_train": rmse_train,
        "r2_train": r2_train,
        "rmse_test": rmse_test,
        "r2_test": r2_test
    }

# Evaluate the models using each set of features in the feature list
results = []

for feature_set in Feature_list:
    print(f"Evaluating feature set: {feature_set}")
    result = evaluate_fastai_model(feature_set)
    results.append(result)

# Create a DataFrame to store the results
results_df = pd.DataFrame(results)

# Display the results
print(results_df.head())

# Save the results to a CSV file
results_df.to_csv("/content/drive/MyDrive/datasets_Rayeed_GSV_POI_LU/fastai_feature_selection_results.csv", index=False)


[I 2024-09-02 20:49:16,210] A new study created in memory with name: Fastai_NN_RMSE


Evaluating feature set: ['RdAll_150', 'gsv_house_p750', 'gsv_signboard_p250', 'RdclP_150', 'gsv_plant_p250']


<ipython-input-14-dfeb0034ff5d>:26: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use suggest_float(..., log=True) instead.
  learning_rate = trial.suggest_loguniform('learning_rate', 1e-5, 1e-1)


/usr/local/lib/python3.10/dist-packages/fastprogress/fastprogress.py:73: UserWarning: Your generator is empty.
  warn("Your generator is empty.")
/usr/local/lib/python3.10/dist-packages/fastprogress/fastprogress.py:73: UserWarning: Your generator is empty.
  warn("Your generator is empty.")
/usr/local/lib/python3.10/dist-packages/fastprogress/fastprogress.py:73: UserWarning: Your generator is empty.
  warn("Your generator is empty.")
/usr/local/lib/python3.10/dist-packages/fastprogress/fastprogress.py:73: UserWarning: Your generator is empty.
  warn("Your generator is empty.")
/usr/local/lib/python3.10/dist-packages/fastprogress/fastprogress.py:73: UserWarning: Your generator is empty.
  warn("Your generator is empty.")
/usr/local/lib/python3.10/dist-packages/fastprogress/fastprogress.py:73: UserWarning: Your generator is empty.
  warn("Your generator is empty.")
/usr/local/lib/python3.10/dist-packages/fastprogress/fastprogress.py:73: UserWarning: Your generator is empty.
  warn("Your 

[I 2024-09-02 20:49:16,938] Trial 0 finished with value: 62484.51435450453 and parameters: {'n_layers': 1, 'n_units_l0': 428, 'learning_rate': 0.0005603828139632424}. Best is trial 0 with value: 62484.51435450453.
<ipython-input-14-dfeb0034ff5d>:26: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use suggest_float(..., log=True) instead.
  learning_rate = trial.suggest_loguniform('learning_rate', 1e-5, 1e-1)


...

[I 2024-09-02 20:52:33,650] Trial 98 finished with value: 59575.461834745896 and parameters: {'n_layers': 1, 'n_units_l0': 184, 'learning_rate': 0.004899053305399076}. Best is trial 49 with value: 55446.24962791465.
<ipython-input-14-dfeb0034ff5d>:26: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use suggest_float(..., log=True) instead.
  learning_rate = trial.suggest_loguniform('learning_rate', 1e-5, 1e-1)


/usr/local/lib/python3.10/dist-packages/fastprogress/fastprogress.py:73: UserWarning: Your generator is empty.
  warn("Your generator is empty.")
/usr/local/lib/python3.10/dist-packages/fastprogress/fastprogress.py:73: UserWarning: Your generator is empty.
  warn("Your generator is empty.")
/usr/local/lib/python3.10/dist-packages/fastprogress/fastprogress.py:73: UserWarning: Your generator is empty.
  warn("Your generator is empty.")
/usr/local/lib/python3.10/dist-packages/fastprogress/fastprogress.py:73: UserWarning: Your generator is empty.
  warn("Your generator is empty.")
/usr/local/lib/python3.10/dist-packages/fastprogress/fastprogress.py:73: UserWarning: Your generator is empty.
  warn("Your generator is empty.")
/usr/local/lib/python3.10/dist-packages/fastprogress/fastprogress.py:73: UserWarning: Your generator is empty.
  warn("Your generator is empty.")
/usr/local/lib/python3.10/dist-packages/fastprogress/fastprogress.py:73: UserWarning: Your generator is empty.
  warn("Your 

[I 2024-09-02 20:52:34,036] Trial 99 finished with value: 61050.03735276978 and parameters: {'n_layers': 1, 'n_units_l0': 356, 'learning_rate': 0.008742218390751464}. Best is trial 49 with value: 55446.24962791465.


/usr/local/lib/python3.10/dist-packages/fastprogress/fastprogress.py:73: UserWarning: Your generator is empty.
  warn("Your generator is empty.")
/usr/local/lib/python3.10/dist-packages/fastprogress/fastprogress.py:73: UserWarning: Your generator is empty.
  warn("Your generator is empty.")
/usr/local/lib/python3.10/dist-packages/fastprogress/fastprogress.py:73: UserWarning: Your generator is empty.
  warn("Your generator is empty.")
/usr/local/lib/python3.10/dist-packages/fastprogress/fastprogress.py:73: UserWarning: Your generator is empty.
  warn("Your generator is empty.")
/usr/local/lib/python3.10/dist-packages/fastprogress/fastprogress.py:73: UserWarning: Your generator is empty.
  warn("Your generator is empty.")
/usr/local/lib/python3.10/dist-packages/fastprogress/fastprogress.py:73: UserWarning: Your generator is empty.
  warn("Your generator is empty.")
/usr/local/lib/python3.10/dist-packages/fastprogress/fastprogress.py:73: UserWarning: Your generator is empty.
  warn("Your 

                                                                     features  \
0  [RdAll_150, gsv_house_p750, gsv_signboard_p250, RdclP_150, gsv_plant_p250]   
1                      [RdAll_150, gsv_house_p750, RdclP_150, gsv_plant_p250]   
2       [RdAll_150, gsv_house_p750, gsv_bus_p1000, RdclP_150, gsv_plant_p250]   
3       [RdAll_150, gsv_house_p750, gsv_signboard_p250, RdL3_1000, RdclP_150]   

              model    rmse_train   r2_train     rmse_test   r2_test  
0  Fastai_NeuralNet  58833.456801  -8.645663  64524.908568 -5.927052  
1  Fastai_NeuralNet  59386.908647  -8.511230  64524.597993 -5.926986  
2  Fastai_NeuralNet  61461.242987 -11.093044  64524.637196 -5.926994  
3  Fastai_NeuralNet  58139.742529  -9.116236  64524.674874 -5.927002  
